# Import / Config

In [ ]:
import pandas as pd
from sqlalchemy import create_engine
from neo4j import GraphDatabase

import const as c

## Postgres

In [ ]:
engine = create_engine(
    f'postgresql://{c.pg_userid}:{c.pg_password}@{c.pg_host}/{c.pg_db}', 
    connect_args = {'options': '-c search_path=uadbkt,umobility,public', 'keepalives_idle': 120},
    pool_size=1, 
    max_overflow=0,
    execution_options={ 'isolation_level': 'AUTOCOMMIT' }
)

In [ ]:
# engine.dispose()

In [ ]:
with engine.connect() as con:
    sql = "select * from haltestelle"
    haltestellen_pdf = pd.read_sql_query(sql, con)

In [ ]:
haltestellen_pdf

## neo4j

In [ ]:
cypher = 'MATCH (p:Person) return p.name as name'
with GraphDatabase.driver(c.neo4j_host, auth=(c.neo4j_userid, c.neo4j_password)) as driver:
    with driver.session() as session:
        result = session.run(cypher)
        neo4j_pdf = pd.DataFrame(result.data())

In [ ]:
neo4j_pdf

In [ ]:
cypher_create_stop = 'CREATE (h:Haltestelle {hid: $hid, bez: $bez, lat:$lat, lng:$lng})'
with GraphDatabase.driver(c.neo4j_host, auth=(c.neo4j_userid, c.neo4j_password)) as driver:
    with driver.session() as session:
        for r in haltestellen_pdf.itertuples(index=False):
            session.run(cypher_create_stop, hid=r.hid, bez=r.bez, lat=r.lat, lng=r.lng)

In [ ]:
cypher_read_stops = 'MATCH (h:Haltestelle) return h.hid as hid, h.bez as bez'
with GraphDatabase.driver(c.neo4j_host, auth=(c.neo4j_userid, c.neo4j_password)) as driver:
    with driver.session() as session:
        result = session.run(cypher_read_stops)
        haltestellen_neo4j_pdf = pd.DataFrame(result.data())


In [ ]:
haltestellen_neo4j_pdf